# A. BACKGROUND AND PROBLEM

The problem I want to solve is to find the best possible location(s) to start a ‘mom & pop’ retail shop in the city of Zurich, Switzerland. More specifically, I am looking for the best location for a flower shop, as this will help a friend who is about to launch her flower business.

Location is a key success factor for both pillars of such a business, which are:
- Selling flowers to customers visiting the shop;
- Delivering flowers, ordered either by internet or over phone.

Finding the best location is thus very important for the future business owner. Also, it is important to be able to explain and demonstrate why a specific location is suitable, to convince potential investors and banks of the viability of the future business. So this data visualization exercise is interesting for the business owner, her investors / partners, as well as the bank(s) expected to extend a credit line to the future business.

More specifically, the ideal location should have the following characteristics: 
a)	In a densely populated district of the city (we assume here that purchasing power and propensity to buy flowers is similar in each district, so that only the population density matters).
b)	Near high-traffic public transportation hubs. Zurich mostly relies on a tram system, so that means the shop should be located near the tram stops with the highest number of daily passengers.
c)	In a quite central area of the city, so that most of the city is a quickly reachable for deliveries. A location at the periphery would severely restrict the delivery business’ potential. 
d)	At least 300 meters away from the next flower shop. Being closer from established competition would make it difficult to establish a new business. On the other hand, finding a ‘white space’ away from any competitor may help a lot.
e)	Ideally - but only if all other criteria are met - the shop should be in a pedestrian area, as (i) passerby are more relaxed and more inclined to shop flowers in pedestrian areas and (ii) this brings nicer working conditions for the shop’s employees.

-------

# B. DATA AND HOW IT WILL BE USED TO SOLVE THE PROBLEM

To solve this problem, I will mostly use data from three sources: 
- The folium library 
- The Open Data catalogue of Zurich City (https://data.stadt-zuerich.ch, in German)
- Foursquare.com

This location problem should be easier to solve visually, rather than using formulas with quantitative outputs.  In that context, the folium will help a lot, with the following features:
a)	Background map of the city of Zurich
b)	Various overlays, like the map of the districts, markers for the main tram stations, etc…

The Open Data catalogue of Zurich City will provide us with the following data:
a)	Population of the city, with a split per city district;
b)	Limits of the city districts (geoJSON file). This will allow us to display the districts on the map, and create a choropleth based on the population density;
c)	Limits of the pedestrian areas;
d)	Location and daily number traffic of the tram stations. We will focus on the 20 most busy stations and mark them on the map.

The Foursquare API will provide us with:
a)	The list of existing flower shops in the city of Zurich;
b)	Their location, so that we can display them on the map with a marker;
c)	If needed, additional information on select competitors, like rating and tips…

-----

## 1. DOWNLOAD REQUIRED LIBRARIES

In [1]:
# Download required libraries

import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

#!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

#!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library


print('Libraries imported.')

Libraries imported.


## 2. CREATE A BACKGROUND MAP OF ZURICH

In [2]:
# Install folium 

#!conda install -c conda-forge folium=0.5.0 --yes
#import folium

#print('Folium installed and imported!')

In [3]:
# Get the geo coordinates on Zürich

address = 'Zürich Hardbrücke'

geolocator = Nominatim(user_agent="zh_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print("The geographical coordinates of Zürich are {}, {}.".format(latitude, longitude))

The geographical coordinates of Zürich are 47.3851609, 8.5173926.


In [4]:
# Create a map centered on Zurich city

# define the world map centered around Canada with a higher zoom level
zuri_map1 = folium.Map(location=[latitude, longitude], zoom_start=12)

# display the map
zuri_map1

# 3. OBTAIN DATA ON POPULATION PER DISTRICT

In [5]:
# Download the csv file with the population per disctrict

!wget -q -O 'Zuri_population.csv' https://data.stadt-zuerich.ch/dataset/3168b842-50f7-4cd9-9318-984de65ba1eb/resource/96ed8663-73fa-445b-84d6-749b36063acb/download/bev336od3361.csv
print('Data downloaded!')

Data downloaded!


In [6]:
# Create the dataframe with the population

zuri_pop = pd.read_csv('Zuri_population.csv')
zuri_pop.head(10)

StichtagDatJahr  QuarSort  QuarCd QuarLang  NationHistSort  \
0             1993        11      11  Rathaus            8100   
1             1993        11      11  Rathaus            8205   
2             1993        11      11  Rathaus            8206   
3             1993        11      11  Rathaus            8207   
4             1993        11      11  Rathaus            8211   
5             1993        11      11  Rathaus            8212   
6             1993        11      11  Rathaus            8214   
7             1993        11      11  Rathaus            8215   
8             1993        11      11  Rathaus            8216   
9             1993        11      11  Rathaus            8218   

    NationHistLang  NationSort       NationLang  RegionSort     RegionLang  \
0          Schweiz        8100          Schweiz          13  Zentraleuropa   
1        Bulgarien        8205        Bulgarien          17   Südosteuropa   
2         Dänemark        8206         Dänemark          11     Nordeuropa   
3      Deutschland        8207      Deutschland          13  Zentraleuropa   
4         Finnland        8211         Finnland          11     Nordeuropa   
5       Frankreich        8212       Frankreich          14     Westeuropa   
6     Griechenland        8214     Griechenland          16      Südeuropa   
7  Grossbritannien        8215  Grossbritannien          14     Westeuropa   
8           Irland        8216           Irland          14     Westeuropa   
9          Italien        8218          Italien          16      Südeuropa   

   KontinentSort KontinentLang  AnzBestWir  
0              1        Europa        2487  
1              1        Europa           1  
2              1        Europa           2  
3              1        Europa          96  
4              1        Europa           2  
5              1        Europa          22  
6              1        Europa           1  
7              1        Europa          18  
8              1        Europa           2  
9              1        Europa          69

In [7]:
# Check the shape

zuri_pop.shape

(82144, 13)

In [8]:
# Check the data types

zuri_pop.dtypes

StichtagDatJahr     int64
QuarSort            int64
QuarCd              int64
QuarLang           object
NationHistSort      int64
NationHistLang     object
NationSort          int64
NationLang         object
RegionSort          int64
RegionLang         object
KontinentSort       int64
KontinentLang      object
AnzBestWir          int64
dtype: object

In [9]:
# Prepare the dataframe

# Clean up the dataset to remove unnecessary columns  
zuri_pop.drop(['NationHistSort','NationHistLang','NationSort','NationLang','RegionSort', 'RegionLang', 'KontinentSort', 'KontinentLang'], axis = 1, inplace = True)

# Keep only the 2018 data
# zuri_pop = zuri_pop[zuri_pop['StichtagDatJahr'].str.contains('1993')].reset_index(drop=True)
zuri_pop = zuri_pop[zuri_pop.StichtagDatJahr == 2018].reset_index(drop=True)

# Remove the column with the years
zuri_pop.drop(['StichtagDatJahr'], axis = 1, inplace = True)


# Translate the columns names into English 
#dfcou.rename (columns = {'bis':'until', 'fk_zaehler':'counter_ID','von':'from', 'easting_wgs':'longitude', 'northing_wgs':'latitude'}, inplace = True)

# For sake of consistency, let's also make all column labels of type string
#zuri_pop.columns = list(map(str, zuri_pop.columns))

In [10]:
zuri_pop.head(10)

QuarSort  QuarCd QuarLang  AnzBestWir
0        11      11  Rathaus        2284
1        11      11  Rathaus          17
2        11      11  Rathaus           7
3        11      11  Rathaus           5
4        11      11  Rathaus         257
5        11      11  Rathaus           5
6        11      11  Rathaus          61
7        11      11  Rathaus          17
8        11      11  Rathaus          40
9        11      11  Rathaus           8

In [11]:
# Check the shape

zuri_pop.shape

(3477, 4)

In [12]:
# Count the population per quartier

zuri_pop_grouped=zuri_pop.groupby(['QuarSort','QuarCd'])['AnzBestWir'].sum().reset_index() # if reset_index is not included, groupby does not return a dataframe
zuri_pop_grouped.head()

QuarSort  QuarCd  AnzBestWir
0        11      11        3267
1        12      12         664
2        13      13         990
3        14      14         829
4        21      21       18923

**NOTE:** 
- 'QuarSort' and 'QuarCd' are duplicative in the source dataset, and mean 'district code'
- 'AnzBestWir' gives the population per area

## 4. CREATE A CHOROPLETH BASED ON THE CITY DISTRICTS' POPULATION 

In [13]:
# download the json file

!wget --quiet https://data.stadt-zuerich.ch/dataset/statistisches_quartier/resource/c837926e-035d-48b9-8656-03f1b13c323b/download/statistische_quartiere.json
    
print('GeoJSON file downloaded!')

GeoJSON file downloaded!


In [14]:
# Get geo_data with the districts

with open('statistische_quartiere.json') as json_data:
    zuri_geo = json.load(json_data)
    
    

    

In [15]:
zuri_geo

{'name': 'StatistischesQuartier',
 'type': 'FeatureCollection',
 'features': [{'type': 'Feature',
   'geometry': {'type': 'MultiPolygon',
    'coordinates': [[[[8.47023638671907, 47.3739506414208],
       [8.47033673166121, 47.3739588752243],
       [8.47053472534719, 47.3741281383317],
       [8.47065295785768, 47.3742292747057],
       [8.47072580155878, 47.3742915891487],
       [8.47110650589651, 47.3745777282919],
       [8.47136078217231, 47.3747558957459],
       [8.47165560292566, 47.3749625741451],
       [8.47179106624585, 47.3750575196082],
       [8.47188300088914, 47.3751201932907],
       [8.47187681848969, 47.3751291536723],
       [8.47180175260936, 47.3752385750228],
       [8.47214842904971, 47.3754279676684],
       [8.47257851266964, 47.3756231701708],
       [8.47284880074573, 47.3757449721048],
       [8.47338651894776, 47.3759441642244],
       [8.47333552303066, 47.3759645899739],
       [8.47335127818153, 47.3759774017055],
       [8.47336699216698, 47.37598877

In [16]:
# generate choropleth map using the population per district
zuri_map1.choropleth(
    geo_data=zuri_geo,
    data=zuri_pop_grouped,
    columns=['QuarCd', 'AnzBestWir'],
    key_on='feature.properties.qnr',
    fill_color='YlOrRd', 
    fill_opacity=0.4, 
    line_opacity=0.2,
    legend_name='Population per district'
)

# display map
zuri_map1

# 5. ADD THE PEDESTRIAN AREAS TO THE MAP

In [17]:
# download the json file

!wget --quiet https://data.stadt-zuerich.ch/dataset/fussgaengerzone/resource/69c89d35-cc1d-4a03-8abd-93f726eb4bed/download/fussgaengerzone.json
    
print('GeoJSON file downloaded!')

GeoJSON file downloaded!


In [18]:
# Get geo_data with the districts

with open('fussgaengerzone.json') as json_data:
    zuri_ped = json.load(json_data)

In [19]:
zuri_ped

{'name': 'Fussgaengerzone',
 'type': 'FeatureCollection',
 'features': [{'type': 'Feature',
   'geometry': {'type': 'MultiPolygon',
    'coordinates': [[[[8.54317985515014, 47.374267925821],
       [8.54312625041245, 47.374108072908],
       [8.54306095612084, 47.3740537908475],
       [8.54302190485288, 47.3739214318234],
       [8.54300475025815, 47.3738770158845],
       [8.54298589956456, 47.3737852477082],
       [8.54299147321432, 47.3737596302081],
       [8.54297271117991, 47.3736785294255],
       [8.54295778477066, 47.373586345925],
       [8.54295599928635, 47.373555770494],
       [8.54294656466181, 47.3734416852673],
       [8.54294434547055, 47.3734112668989],
       [8.54293337504005, 47.3732709844837],
       [8.54294626360593, 47.3732705644232],
       [8.5429517733561, 47.3731913724194],
       [8.54292156494485, 47.3731355494802],
       [8.54291824885126, 47.3730457915948],
       [8.54290857665782, 47.3729317356055],
       [8.54290637514617, 47.3729060035365],
   

In [20]:
# Add the limits of the pedestrian district, indicatede with blue lines


#folium.GeoJson(zuri_ped,                         #improved version with a style function
    #style_function=lambda x: {
       # 'color' : x['properties']['stroke'],
     #   'weight' : x['properties']['stroke-width'],
     #  'opacity': 0.6,
     #   'fillColor' : x['properties']['fill'],
    #    }          
     #   ).add_to(zuri_map)

folium.GeoJson(zuri_ped).add_to(zuri_map1)        
        
zuri_map1

# 6. OBTAIN THE LIST OF PUBLIC TRANSPORT STATIONS (TRAMS)

In [21]:
# Download the csv file with the public transportation stations

!wget -q -O 'Zuri_stations.csv' https://data.stadt-zuerich.ch/dataset/vbz_fahrgastzahlen_ogd/resource/8f0ab824-5942-4159-bf2c-ea0cf7dd00b8/download/haltestellen.csv
print('Data downloaded!')

Data downloaded!


In [22]:
# Create the dataframe with the population

zuri_stations = pd.read_csv('Zuri_stations.csv', sep=';' )  # Need to include as separator is not the standard comma in this file
zuri_stations.head(20)

Haltestellen_Id  Haltestellennummer Haltestellenkurzname  \
0               272                6594                 AHOR   
1               270                 148               ABAD01   
2               683                  28               BADL01   
3               273                6593                 EWEG   
4               682                6961                 AGRU   
5               267                6437                 GRUT   
6               271                1227               HOFA01   
7               269                1462               KROA01   
8               680                6592                 ADMO   
9               268                2660               TIAK01   
10              518                6600                 IMBR   
11              519                6599                 ZOLL   
12              585                 445                 BEBO   
13              584                 446                 BGER   
14              513                6778                 BLAN   
15              569                 425                 DBAL   
16              567                 457                 BERL   
17              566                 466                 BOLD   
18              570                 729                 DUEN   
19              510                6855                 GAL2   

             Haltestellenlangname  
0              Adliswil, Ahornweg  
1            Adliswil, Badstrasse  
2               Adliswil, Bahnhof  
3             Adliswil, Eichenweg  
4          Adliswil, Grundstrasse  
5                  Adliswil, Grüt  
6       Adliswil, Hofackerstrasse  
7                 Adliswil, Krone  
8                  Adliswil, Moos  
9             Adliswil, Tiefacker  
10    Aesch bei Maur, Im Brünneli  
11  Aesch bei Maur, Zollingerheim  
12            Benglen, Bodenacher  
13         Benglen, Gerlisbrunnen  
14               Benglen, Langwis  
15     Bergdietikon, Baltenschwil  
16           Bergdietikon, Bergli  
17          Bergdietikon, Bernold  
18            Bergdietikon, Dünni  
19    Bergdietikon, Garage 2 LIBU

**NOTE:** 
- 'Haltestellen' means 'station', or 'stop'
- 'Haltestellennummer' is the station's number
- 'Haltestellenkurzname' is the station's short name
- 'Haltestellenlangname' is the station's long name

In [23]:
# Check the shape

zuri_stations.describe(include='all')

Haltestellen_Id  Haltestellennummer Haltestellenkurzname  \
count        763.000000          763.000000                  763   
unique              NaN                 NaN                  763   
top                 NaN                 NaN                 GOBI   
freq                NaN                 NaN                    1   
mean         385.095675         2618.559633                  NaN   
std          221.755872         2261.051163                  NaN   
min            3.000000            4.000000                  NaN   
25%          193.500000         1159.000000                  NaN   
50%          384.000000         2055.000000                  NaN   
75%          577.500000         3128.000000                  NaN   
max          771.000000        13002.000000                  NaN   

       Haltestellenlangname  
count                   763  
unique                  762  
top         Zürich, Rennweg  
freq                      2  
mean                    NaN  
std                     NaN  
min                     NaN  
25%                     NaN  
50%                     NaN  
75%                     NaN  
max                     NaN

In [24]:
# Check the data types

zuri_stations.dtypes

Haltestellen_Id          int64
Haltestellennummer       int64
Haltestellenkurzname    object
Haltestellenlangname    object
dtype: object

In [25]:
zuri_stations.head()

Haltestellen_Id  Haltestellennummer Haltestellenkurzname  \
0              272                6594                 AHOR   
1              270                 148               ABAD01   
2              683                  28               BADL01   
3              273                6593                 EWEG   
4              682                6961                 AGRU   

     Haltestellenlangname  
0      Adliswil, Ahornweg  
1    Adliswil, Badstrasse  
2       Adliswil, Bahnhof  
3     Adliswil, Eichenweg  
4  Adliswil, Grundstrasse

# 7. OBTAIN THE DAILY PASSENGERS TRAFFIC STATISTIC PER STATION FOR THE YEAR 2018 

In [26]:
# Download the csv file with the public transportation traffic for 2018

!wget -q -O 'Zuri_transport_traffic.csv' https://data.stadt-zuerich.ch/dataset/vbz_fahrgastzahlen_ogd/resource/ea1e9d1e-e447-49b1-bf51-b8f1e5819bf3/download/reisende.csv
print('Data downloaded!')

Data downloaded!


In [27]:
# Create the dataframe with the statistics of public transportation passengers for 2018

zuri_trans = pd.read_csv('Zuri_transport_traffic.csv', sep = ';')
zuri_trans.head(10)

Tagtyp_Id  Linien_Id  Linienname  Plan_Fahrt_Id  Richtung  Sequenz  \
0         15         60         704          91534         2        1   
1         15         60         704          91534         2        2   
2         15         60         704          91534         2        3   
3         15         60         704          91534         2        4   
4         15         60         704          91534         2        5   
5         15         60         704          91534         2        6   
6         15         60         704          91534         2        7   
7         15         60         704          91534         2        8   
8         15         60         704          91534         2        9   
9         15         60         704          91534         2       10   

   Haltestellen_Id  Nach_Hst_Id     FZ_AB  Anzahl_Messungen  Einsteiger  \
0              576        575.0  05:38:00                11        4.63   
1              575        574.0  05:39:54                11        0.00   
2              574        451.0  05:41:12                11        0.09   
3              451        511.0  05:42:48                11        1.63   
4              511        512.0  05:44:00                11        0.09   
5              512        577.0  05:45:12                11        0.00   
6              577        578.0  05:46:18                11        2.72   
7              578        579.0  05:47:12                11        0.45   
8              579        580.0  05:48:12                11        1.09   
9              580        581.0  05:49:00                11        0.45   

   Aussteiger  Besetzung  Distanz  Tage_DTV  Tage_DWV  Tage_SA  Tage_SO  \
0        0.00       4.63   1150.0     100.4     100.4      0.0      0.0   
1        0.00       4.63    834.0     100.4     100.4      0.0      0.0   
2        1.63       3.09    690.0     100.4     100.4      0.0      0.0   
3        1.27       3.45    478.0     100.4     100.4      0.0      0.0   
4        0.00       3.54    720.0     100.4     100.4      0.0      0.0   
5        0.00       3.54    458.0     100.4     100.4      0.0      0.0   
6        0.00       6.27    400.0     100.4     100.4      0.0      0.0   
7        0.00       6.72    506.0     100.4     100.4      0.0      0.0   
8        0.00       7.81    250.0     100.4     100.4      0.0      0.0   
9        0.09       8.18   1133.0     100.4     100.4      0.0      0.0   

   Nachtnetz  Tage_SA_N  Tage_SO_N  ID_Abschnitt  
0          0          0          0      57600575  
1          0          0          0      57500574  
2          0          0          0      57400451  
3          0          0          0      45100511  
4          0          0          0      51100512  
5          0          0          0      51200577  
6          0          0          0      57700578  
7          0          0          0      57800579  
8          0          0          0      57900580  
9          0          0          0      58000581

In [28]:
# Check the shape
zuri_trans.describe(include='all')
zuri_trans.shape

(910781, 22)

In [29]:
zuri_trans.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 910781 entries, 0 to 910780
Data columns (total 22 columns):
Tagtyp_Id           910781 non-null int64
Linien_Id           910781 non-null int64
Linienname          910781 non-null int64
Plan_Fahrt_Id       910781 non-null int64
Richtung            910781 non-null int64
Sequenz             910781 non-null int64
Haltestellen_Id     910781 non-null int64
Nach_Hst_Id         863248 non-null float64
FZ_AB               910781 non-null object
Anzahl_Messungen    910781 non-null int64
Einsteiger          910755 non-null float64
Aussteiger          910755 non-null float64
Besetzung           863226 non-null float64
Distanz             863248 non-null float64
Tage_DTV            910781 non-null float64
Tage_DWV            910781 non-null float64
Tage_SA             910781 non-null float64
Tage_SO             910781 non-null float64
Nachtnetz           910781 non-null int64
Tage_SA_N           910781 non-null int64
Tage_SO_N           910781 non

In [30]:
#Keep only the required columns

zuri_trans = zuri_trans[['Haltestellen_Id', 'Einsteiger', 'Aussteiger']]
zuri_trans.head()

Haltestellen_Id  Einsteiger  Aussteiger
0              576        4.63        0.00
1              575        0.00        0.00
2              574        0.09        1.63
3              451        1.63        1.27
4              511        0.09        0.00

**NOTE:**
- 'Einsteiger' are passengers getting into the tram
- 'Austeiger' are passengers getting out of the tram

In [31]:
# Add a 'Passengers' column, sum of passengers leaving and joining the bus

zuri_trans['Passengers'] = 0  # Initiate the 'Passengers' column with zeroes

zuri_trans.iloc[:,-1]= zuri_trans.iloc[:,-2] + zuri_trans.iloc[:,-3]

zuri_trans.head()

Haltestellen_Id  Einsteiger  Aussteiger  Passengers
0              576        4.63        0.00        4.63
1              575        0.00        0.00        0.00
2              574        0.09        1.63        1.72
3              451        1.63        1.27        2.90
4              511        0.09        0.00        0.09

**NOTE:**
- Here we add the passengers getting in the tram to the passengers getting out, to get the total number of passengers for a given station

In [32]:
# Calculate the total number of passenger for each station for the whole 2018

zuri_trans_grouped = zuri_trans.groupby(['Haltestellen_Id']).sum().reset_index() # if reset_index is not included, groupby does not return a dataframe
zuri_trans_grouped.head()

Haltestellen_Id  Einsteiger  Aussteiger  Passengers
0                4    16482.38    15044.61    31526.99
1                5      139.51      151.20      290.71
2                6      507.74      472.18      979.92
3                7      964.77      861.10     1825.87
4                8      715.36      796.65     1512.01

In [33]:
zuri_trans_grouped.describe(include='all')

Haltestellen_Id     Einsteiger     Aussteiger     Passengers
count       748.000000     748.000000     748.000000     748.000000
mean        386.921123    4917.746840    4928.517669    9846.264509
std         221.230605   12062.333549   11597.387585   23634.867193
min           4.000000       0.000000       0.000000       0.630000
25%         195.750000     152.360000     190.377500     355.087500
50%         386.500000     784.860000     859.805000    1647.955000
75%         579.250000    4161.425000    4213.435000    8169.925000
max         771.000000  118270.820000  102521.240000  220792.060000

In [34]:
# Drop the columns we don't need anymore

zuri_trans_grouped.drop(['Einsteiger','Aussteiger'], axis = 1, inplace = True)

In [35]:
zuri_trans_grouped.head()

Haltestellen_Id  Passengers
0                4    31526.99
1                5      290.71
2                6      979.92
3                7     1825.87
4                8     1512.01

In [36]:
# Convert the numbers of passengers to integers

zuri_trans_grouped['Passengers'] = zuri_trans_grouped['Passengers'].astype("int")

In [37]:
# Join the zuri_trans_grouped and zuri_stations dtaframes, using 'Haltestellen_Id' as the key 

#dfj = zuri_stations.join(zuri_trans_grouped.set_index('Haltestellen_Id'), on='Haltestellen_Id')
dfm = zuri_stations.merge(zuri_trans_grouped, on='Haltestellen_Id', how='left')
dfm.head(10)

Haltestellen_Id  Haltestellennummer Haltestellenkurzname  \
0              272                6594                 AHOR   
1              270                 148               ABAD01   
2              683                  28               BADL01   
3              273                6593                 EWEG   
4              682                6961                 AGRU   
5              267                6437                 GRUT   
6              271                1227               HOFA01   
7              269                1462               KROA01   
8              680                6592                 ADMO   
9              268                2660               TIAK01   

        Haltestellenlangname  Passengers  
0         Adliswil, Ahornweg       508.0  
1       Adliswil, Badstrasse       590.0  
2          Adliswil, Bahnhof      2311.0  
3        Adliswil, Eichenweg       455.0  
4     Adliswil, Grundstrasse        98.0  
5             Adliswil, Grüt       476.0  
6  Adliswil, Hofackerstrasse       463.0  
7            Adliswil, Krone       135.0  
8             Adliswil, Moos       112.0  
9        Adliswil, Tiefacker       273.0

In [38]:
dfm.describe(include='all')

Haltestellen_Id  Haltestellennummer Haltestellenkurzname  \
count        763.000000          763.000000                  763   
unique              NaN                 NaN                  763   
top                 NaN                 NaN                 GOBI   
freq                NaN                 NaN                    1   
mean         385.095675         2618.559633                  NaN   
std          221.755872         2261.051163                  NaN   
min            3.000000            4.000000                  NaN   
25%          193.500000         1159.000000                  NaN   
50%          384.000000         2055.000000                  NaN   
75%          577.500000         3128.000000                  NaN   
max          771.000000        13002.000000                  NaN   

       Haltestellenlangname     Passengers  
count                   763     748.000000  
unique                  762            NaN  
top         Zürich, Rennweg            NaN  
freq                      2            NaN  
mean                    NaN    9845.759358  
std                     NaN   23634.882118  
min                     NaN       0.000000  
25%                     NaN     354.750000  
50%                     NaN    1647.500000  
75%                     NaN    8169.250000  
max                     NaN  220792.000000

In [39]:
dfm.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 763 entries, 0 to 762
Data columns (total 5 columns):
Haltestellen_Id         763 non-null int64
Haltestellennummer      763 non-null int64
Haltestellenkurzname    763 non-null object
Haltestellenlangname    763 non-null object
Passengers              748 non-null float64
dtypes: float64(1), int64(2), object(2)
memory usage: 35.8+ KB


In [40]:
# Sort by number of passengers, descending order, and focus on top 20 stations

dfm.sort_values(by=['Passengers'], ascending = False, axis = 0, inplace = True, na_position='last') #Note: 'by=' needed, if not the code does not return a dataframe 
dfm.reset_index(drop=True)
zuri_top_stations = dfm.head(20).reset_index(drop=True)
zuri_top_stations

Haltestellen_Id  Haltestellennummer Haltestellenkurzname  \
0                22                 440                 BELL   
1               244                 412                 BPLA   
2               114                 416                 BSTR   
3               116                1861                 PARA   
4               113                 413                 BQUA   
5               248                 619                 CENT   
6               141                2556                 STAU   
7                72                3022                 BALT   
8               153                  48                 ALBP   
9               119                3039                 BSTA   
10              241                1557                 LIMM   
11              107                 564                 BUCH   
12              129                1643                 MIBU   
13              169                3029                 HSBB   
14              115                2054                 RAUG   
15               49                2572                 SOER   
16              358                1430                 KLUS   
17              109                2158                 SPLA   
18               60                3034                 BOER   
19              171                 799                 EWYS   

           Haltestellenlangname  Passengers  
0              Zürich, Bellevue    220792.0  
1       Zürich, Bahnhofplatz/HB    194430.0  
2     Zürich, Bahnhofstrasse/HB    185631.0  
3           Zürich, Paradeplatz    177712.0  
4        Zürich, Bahnhofquai/HB    158253.0  
5               Zürich, Central    155332.0  
6           Zürich, Stauffacher    154432.0  
7    Zürich, Bahnhof Altstetten    125998.0  
8      Zürich, Albisriederplatz    121837.0  
9   Zürich, Bahnhof Stadelhofen    120800.0  
10          Zürich, Limmatplatz    113822.0  
11         Zürich, Bucheggplatz    104558.0  
12            Zürich, Milchbuck    100554.0  
13   Zürich, Bahnhof Hardbrücke     95359.0  
14              Zürich, Rennweg     88945.0  
15     Zürich, Sternen Oerlikon     88837.0  
16            Zürich, Klusplatz     87824.0  
17    Zürich, Schaffhauserplatz     78776.0  
18     Zürich, Bahnhof Oerlikon     76366.0  
19    Zürich, Escher-Wyss-Platz     75955.0

# 8. ADD THE TOP STATIONS TO THE MAP

In [41]:
# Download the csv file with the coordinates of the public transportation stations

!wget -q -O 'Zuri_stops.txt' https://data.stadt-zuerich.ch/dataset/eb393743-5b0d-46f1-89b1-fdfaf55ad7c0/resource/f1331d60-49ac-4c53-905c-3b8e536a74e0/download/stops.txt
print('Data downloaded!')

Data downloaded!


In [42]:
# Create the dataframe with the stops

zuri_stops = pd.read_csv('Zuri_stops.txt', sep=',' )  # Need to include as spearate is not the standard comma
zuri_stops.head()

stop_id                 stop_name   stop_lat  stop_lon  \
0  ch:23026:1167:1:51  Pfäffikon ZH, Hermatswil  47.394282  8.826199   
1  ch:23026:1291:1:60   Hüntwangen-Wil, Bahnhof  47.581424  8.513460   
2  ch:23026:1291:1:61   Hüntwangen-Wil, Bahnhof  47.581272  8.513325   
3  ch:23026:1291:1:62   Hüntwangen-Wil, Bahnhof  47.581030  8.513145   
4  ch:23026:1458:1:52       Turbenthal, Schloss  47.435641  8.847337   

                                            stop_url  location_type  \
0  http://online.fahrplan.zvv.ch/bin/stboard.exe/...            NaN   
1  http://online.fahrplan.zvv.ch/bin/stboard.exe/...            NaN   
2  http://online.fahrplan.zvv.ch/bin/stboard.exe/...            NaN   
3  http://online.fahrplan.zvv.ch/bin/stboard.exe/...            NaN   
4  http://online.fahrplan.zvv.ch/bin/stboard.exe/...            NaN   

  parent_station  
0            NaN  
1     Parent1291  
2     Parent1291  
3     Parent1291  
4            NaN

In [43]:
zuri_stops.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5825 entries, 0 to 5824
Data columns (total 7 columns):
stop_id           5825 non-null object
stop_name         5825 non-null object
stop_lat          5825 non-null float64
stop_lon          5825 non-null float64
stop_url          5320 non-null object
location_type     505 non-null float64
parent_station    1674 non-null object
dtypes: float64(3), object(4)
memory usage: 318.6+ KB


In [44]:
zuri_stops.describe(include='all')

stop_id stop_name     stop_lat     stop_lon  \
count                  5825      5825  5825.000000  5825.000000   
unique                 5825      2914          NaN          NaN   
top     gen:23026:6676:1:50   Bahnhof          NaN          NaN   
freq                      1        49          NaN          NaN   
mean                    NaN       NaN    47.381803     8.615049   
std                     NaN       NaN     0.093831     0.126322   
min                     NaN       NaN    47.173171     8.339806   
25%                     NaN       NaN    47.316032     8.526476   
50%                     NaN       NaN    47.382878     8.590751   
75%                     NaN       NaN    47.431509     8.711305   
max                     NaN       NaN    47.698749     8.995828   

                                                 stop_url  location_type  \
count                                                5320          505.0   
unique                                               2517            NaN   
top     http://online.fahrplan.zvv.ch/bin/stboard.exe/...            NaN   
freq                                                   18            NaN   
mean                                                  NaN            1.0   
std                                                   NaN            0.0   
min                                                   NaN            1.0   
25%                                                   NaN            1.0   
50%                                                   NaN            1.0   
75%                                                   NaN            1.0   
max                                                   NaN            1.0   

       parent_station  
count            1674  
unique            505  
top        Parent3027  
freq               18  
mean              NaN  
std               NaN  
min               NaN  
25%               NaN  
50%               NaN  
75%               NaN  
max               NaN

In [45]:
# Remove the colimns we don't need

zuri_stops.drop(['stop_url','location_type'], axis = 1, inplace = True)

In [46]:
# Keep only the rows with a 'parent station'

zuri_stops = zuri_stops[zuri_stops['parent_station'].str.contains('NaN') == False]
zuri_stops.head()

stop_id                stop_name   stop_lat  stop_lon  \
1  ch:23026:1291:1:60  Hüntwangen-Wil, Bahnhof  47.581424  8.513460   
2  ch:23026:1291:1:61  Hüntwangen-Wil, Bahnhof  47.581272  8.513325   
3  ch:23026:1291:1:62  Hüntwangen-Wil, Bahnhof  47.581030  8.513145   
5  ch:23026:1617:1:51       Marthalen, Bahnhof  47.631754  8.656148   
6  ch:23026:1617:1:52       Marthalen, Bahnhof  47.631899  8.656103   

  parent_station  
1     Parent1291  
2     Parent1291  
3     Parent1291  
5     Parent1617  
6     Parent1617

In [47]:
# Remove the 'Parent' characters in the last column string

zuri_stops['parent_station'] = zuri_stops['parent_station'].str.lstrip('Parent')  # strip / remove characters from the string
zuri_stops.head()

stop_id                stop_name   stop_lat  stop_lon  \
1  ch:23026:1291:1:60  Hüntwangen-Wil, Bahnhof  47.581424  8.513460   
2  ch:23026:1291:1:61  Hüntwangen-Wil, Bahnhof  47.581272  8.513325   
3  ch:23026:1291:1:62  Hüntwangen-Wil, Bahnhof  47.581030  8.513145   
5  ch:23026:1617:1:51       Marthalen, Bahnhof  47.631754  8.656148   
6  ch:23026:1617:1:52       Marthalen, Bahnhof  47.631899  8.656103   

  parent_station  
1           1291  
2           1291  
3           1291  
5           1617  
6           1617

In [48]:
# remove duplicate rows in 'parent_station' column

zuri_stops = zuri_stops.drop_duplicates(subset=['parent_station'], keep='first').reset_index(drop=True)
zuri_stops.head()

stop_id                   stop_name   stop_lat  stop_lon  \
0  ch:23026:1291:1:60     Hüntwangen-Wil, Bahnhof  47.581424  8.513460   
1  ch:23026:1617:1:51          Marthalen, Bahnhof  47.631754  8.656148   
2  ch:23026:1781:1:52       Oberglatt ZH, Bahnhof  47.470375  8.510774   
3  ch:23026:2095:1:52      Dübendorf, Ringstrasse  47.400040  8.607379   
4  ch:23026:2283:2:12  Winterthur, Schulhaus Seen  47.483295  8.761592   

  parent_station  
0           1291  
1           1617  
2           1781  
3           2095  
4           2283

In [49]:
test = zuri_stops[zuri_stops['parent_station']==1430]
test

Empty DataFrame
Columns: [stop_id, stop_name, stop_lat, stop_lon, parent_station]
Index: []

In [50]:
# Convert the 'parent_station' values into integers, so that we can use as key to merge with zuri_top_stations

zuri_stops['parent_station'] = zuri_stops['parent_station'].astype("int")

In [51]:
# Left join the zuri_top_stations and zuri_stops dataframes, using 'Haltestellennummer' and 'parent_station' as the key 


zuri_top_stations_m = zuri_top_stations.merge(zuri_stops, left_on='Haltestellennummer', right_on='parent_station',how='left')
zuri_top_stations_m

Haltestellen_Id  Haltestellennummer Haltestellenkurzname  \
0                22                 440                 BELL   
1               244                 412                 BPLA   
2               114                 416                 BSTR   
3               116                1861                 PARA   
4               113                 413                 BQUA   
5               248                 619                 CENT   
6               141                2556                 STAU   
7                72                3022                 BALT   
8               153                  48                 ALBP   
9               119                3039                 BSTA   
10              241                1557                 LIMM   
11              107                 564                 BUCH   
12              129                1643                 MIBU   
13              169                3029                 HSBB   
14              115                2054                 RAUG   
15               49                2572                 SOER   
16              358                1430                 KLUS   
17              109                2158                 SPLA   
18               60                3034                 BOER   
19              171                 799                 EWYS   

           Haltestellenlangname  Passengers              stop_id  \
0              Zürich, Bellevue    220792.0    gen:23026:440:1:0   
1       Zürich, Bahnhofplatz/HB    194430.0    gen:23026:412:1:0   
2     Zürich, Bahnhofstrasse/HB    185631.0    gen:23026:416:1:0   
3           Zürich, Paradeplatz    177712.0   gen:23026:1861:1:0   
4        Zürich, Bahnhofquai/HB    158253.0    gen:23026:413:1:0   
5               Zürich, Central    155332.0    gen:23026:619:1:0   
6           Zürich, Stauffacher    154432.0   gen:23026:2556:1:0   
7    Zürich, Bahnhof Altstetten    125998.0  gen:23026:3022:1:10   
8      Zürich, Albisriederplatz    121837.0     gen:23026:48:1:0   
9   Zürich, Bahnhof Stadelhofen    120800.0   gen:23026:3039:1:0   
10          Zürich, Limmatplatz    113822.0   gen:23026:1557:1:0   
11         Zürich, Bucheggplatz    104558.0    gen:23026:564:1:0   
12            Zürich, Milchbuck    100554.0   gen:23026:1643:1:0   
13   Zürich, Bahnhof Hardbrücke     95359.0                  NaN   
14              Zürich, Rennweg     88945.0                  NaN   
15     Zürich, Sternen Oerlikon     88837.0   gen:23026:2572:1:0   
16            Zürich, Klusplatz     87824.0   gen:23026:1430:1:0   
17    Zürich, Schaffhauserplatz     78776.0   gen:23026:2158:1:1   
18     Zürich, Bahnhof Oerlikon     76366.0   gen:23026:3034:2:1   
19    Zürich, Escher-Wyss-Platz     75955.0    gen:23026:799:1:0   

                      stop_name   stop_lat  stop_lon  parent_station  
0              Zürich, Bellevue  47.366873  8.545332           440.0  
1       Zürich, Bahnhofplatz/HB  47.377081  8.539771           412.0  
2     Zürich, Bahnhofstrasse/HB  47.375974  8.539340           416.0  
3           Zürich, Paradeplatz  47.369629  8.539125          1861.0  
4        Zürich, Bahnhofquai/HB  47.377379  8.541667           413.0  
5               Zürich, Central  47.376795  8.544101           619.0  
6           Zürich, Stauffacher  47.373596  8.530303          2556.0  
7    Zürich, Bahnhof Altstetten  47.390669  8.489259          3022.0  
8      Zürich, Albisriederplatz  47.378176  8.510513            48.0  
9   Zürich, Bahnhof Stadelhofen  47.366137  8.548117          3039.0  
10          Zürich, Limmatplatz  47.384490  8.531767          1557.0  
11         Zürich, Bucheggplatz  47.398216  8.533330           564.0  
12            Zürich, Milchbuck  47.397480  8.541613          1643.0  
13                          NaN        NaN       NaN             NaN  
14                          NaN        NaN       NaN             NaN  
15     Zürich, Sternen Oerlikon  47.409671  8.546248          2572.0  
16            Zürich, K

In [52]:
# Get and add the geo coordinates Zürich, Bahnhof Hardbrücke

address = 'Zürich, Bahnhof Hardbrücke'

geolocator = Nominatim(user_agent="zh_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
zuri_top_stations_m.iloc[13,-3] = latitude 
zuri_top_stations_m.iloc[13,-2] = longitude
print("The geographical coordinates of Zürich, Bahnhof Hardbrücke are {}, {}.".format(latitude, longitude))

The geographical coordinates of Zürich, Bahnhof Hardbrücke are 47.3852707, 8.5172996.


In [53]:
# Get and add the geo coordinates Zürich, Rennweg

address = 'Zürich, Rennweg'
geolocator = Nominatim(user_agent="zh_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
zuri_top_stations_m.iloc[14,-3] = latitude 
zuri_top_stations_m.iloc[14,-2] = longitude
print("The geographical coordinates of Zürich, Rennweg are {}, {}.".format(latitude, longitude))

The geographical coordinates of Zürich, Rennweg are 47.3729819, 8.5382544.


In [54]:
zuri_top_stations_m

Haltestellen_Id  Haltestellennummer Haltestellenkurzname  \
0                22                 440                 BELL   
1               244                 412                 BPLA   
2               114                 416                 BSTR   
3               116                1861                 PARA   
4               113                 413                 BQUA   
5               248                 619                 CENT   
6               141                2556                 STAU   
7                72                3022                 BALT   
8               153                  48                 ALBP   
9               119                3039                 BSTA   
10              241                1557                 LIMM   
11              107                 564                 BUCH   
12              129                1643                 MIBU   
13              169                3029                 HSBB   
14              115                2054                 RAUG   
15               49                2572                 SOER   
16              358                1430                 KLUS   
17              109                2158                 SPLA   
18               60                3034                 BOER   
19              171                 799                 EWYS   

           Haltestellenlangname  Passengers              stop_id  \
0              Zürich, Bellevue    220792.0    gen:23026:440:1:0   
1       Zürich, Bahnhofplatz/HB    194430.0    gen:23026:412:1:0   
2     Zürich, Bahnhofstrasse/HB    185631.0    gen:23026:416:1:0   
3           Zürich, Paradeplatz    177712.0   gen:23026:1861:1:0   
4        Zürich, Bahnhofquai/HB    158253.0    gen:23026:413:1:0   
5               Zürich, Central    155332.0    gen:23026:619:1:0   
6           Zürich, Stauffacher    154432.0   gen:23026:2556:1:0   
7    Zürich, Bahnhof Altstetten    125998.0  gen:23026:3022:1:10   
8      Zürich, Albisriederplatz    121837.0     gen:23026:48:1:0   
9   Zürich, Bahnhof Stadelhofen    120800.0   gen:23026:3039:1:0   
10          Zürich, Limmatplatz    113822.0   gen:23026:1557:1:0   
11         Zürich, Bucheggplatz    104558.0    gen:23026:564:1:0   
12            Zürich, Milchbuck    100554.0   gen:23026:1643:1:0   
13   Zürich, Bahnhof Hardbrücke     95359.0                  NaN   
14              Zürich, Rennweg     88945.0                  NaN   
15     Zürich, Sternen Oerlikon     88837.0   gen:23026:2572:1:0   
16            Zürich, Klusplatz     87824.0   gen:23026:1430:1:0   
17    Zürich, Schaffhauserplatz     78776.0   gen:23026:2158:1:1   
18     Zürich, Bahnhof Oerlikon     76366.0   gen:23026:3034:2:1   
19    Zürich, Escher-Wyss-Platz     75955.0    gen:23026:799:1:0   

                      stop_name   stop_lat  stop_lon  parent_station  
0              Zürich, Bellevue  47.366873  8.545332           440.0  
1       Zürich, Bahnhofplatz/HB  47.377081  8.539771           412.0  
2     Zürich, Bahnhofstrasse/HB  47.375974  8.539340           416.0  
3           Zürich, Paradeplatz  47.369629  8.539125          1861.0  
4        Zürich, Bahnhofquai/HB  47.377379  8.541667           413.0  
5               Zürich, Central  47.376795  8.544101           619.0  
6           Zürich, Stauffacher  47.373596  8.530303          2556.0  
7    Zürich, Bahnhof Altstetten  47.390669  8.489259          3022.0  
8      Zürich, Albisriederplatz  47.378176  8.510513            48.0  
9   Zürich, Bahnhof Stadelhofen  47.366137  8.548117          3039.0  
10          Zürich, Limmatplatz  47.384490  8.531767          1557.0  
11         Zürich, Bucheggplatz  47.398216  8.533330           564.0  
12            Zürich, Milchbuck  47.397480  8.541613          1643.0  
13                          NaN  47.385271  8.517300             NaN  
14                          NaN  47.372982  8.538254             NaN  
15     Zürich, Sternen Oerlikon  47.409671  8.546248          2572.0  
16            Zürich, K

In [55]:
# Import dropbox urls of numbered custom icons 

icons  = {'icon_numb' : ['https://dl.dropboxusercontent.com/s/j63xv0fyszpvuo6/number_1.png?dl=0', 
                         'https://dl.dropboxusercontent.com/s/6drbpmd3y05ymtl/number_2.png?dl=0',
                         'https://dl.dropboxusercontent.com/s/ucof4kpfztnm2mm/number_3.png?dl=0',
                         'https://dl.dropboxusercontent.com/s/793p0fcjhohocfk/number_4.png?dl=0',
                         'https://dl.dropboxusercontent.com/s/av13oiktz6xnwjm/number_5.png?dl=0',
                         'https://dl.dropboxusercontent.com/s/wq9caoi7rqf7fci/number_6.png?dl=0',
                         'https://dl.dropboxusercontent.com/s/6tx7fmtxa964682/number_7.png?dl=0',
                         'https://dl.dropboxusercontent.com/s/x5xiwvwpfc9lxqo/number_8.png?dl=0',
                         'https://dl.dropboxusercontent.com/s/928793qgqt5h3aa/number_9.png?dl=0',
                         'https://dl.dropboxusercontent.com/s/ynjcgp2g7gx6g51/number_10.png?dl=0',
                         'https://dl.dropboxusercontent.com/s/o0anh340homr836/number_11.png?dl=0',
                         'https://dl.dropboxusercontent.com/s/debyfpr9yrtj8as/number_12.png?dl=0',
                         'https://dl.dropboxusercontent.com/s/cbuczkotx6pbiwe/number_13.png?dl=0',
                         'https://dl.dropboxusercontent.com/s/355y6pjz84y2ib4/number_14.png?dl=0',
                         'https://dl.dropboxusercontent.com/s/o4gfo8ed54aqriz/number_15.png?dl=0',
                         'https://dl.dropboxusercontent.com/s/wzmjtyri3i4vkh5/number_16.png?dl=0',
                         'https://dl.dropboxusercontent.com/s/e05dilvpqahpecc/number_17.png?dl=0',
                         'https://dl.dropboxusercontent.com/s/9z8q2soin0c96e1/number_18.png?dl=0',
                         'https://dl.dropboxusercontent.com/s/ikrr71ahr24hbly/number_19.png?dl=0',
                         'https://dl.dropboxusercontent.com/s/fma97sfww8clqsn/number_20.png?dl=0']}
icons_df = pd.DataFrame(icons)          
icons_df.head()     

icon_numb
0  https://dl.dropboxusercontent.com/s/j63xv0fysz...
1  https://dl.dropboxusercontent.com/s/6drbpmd3y0...
2  https://dl.dropboxusercontent.com/s/ucof4kpfzt...
3  https://dl.dropboxusercontent.com/s/793p0fcjho...
4  https://dl.dropboxusercontent.com/s/av13oiktz6...

In [56]:
icon_sizes = (30,30)

for i in range(20):
    icon_url = icons_df.icon_numb[i]
    Icon = folium.features.CustomIcon(icon_url, icon_size=icon_sizes)
    latitude = zuri_top_stations_m.stop_lat[i]
    longitude = zuri_top_stations_m.stop_lon[i]
    label = '{}, {}k'.format(zuri_top_stations_m.Haltestellenlangname[i], int(zuri_top_stations_m.Passengers [i]//1000))
    folium.Marker([latitude, longitude],icon = Icon,popup = label).add_to(zuri_map1)  

In [57]:
zuri_map1

**NOTE:**
- The number in custom icon indicates the rank of the stop (ie 1 is the stop with highest daily traffic)
- Clicking on an icon allows to see the name of the station, and the daily passenger traffic

# 9. GET FOURSQUARE DATA ON EXISTING FLOWER SHOPS IN ZURICH

In [58]:
# @hidden_cell
# Provide Foursquare credentials

CLIENT_ID = 'XXIS3CL4M12UNBJW4WWAIBB2FH1DFYDSKCFU1N4FXDJBTCFP' # your Foursquare ID
CLIENT_SECRET = 'SILTQ5NCU322DDHLINFUWQ5AS5OI14QX3TVGUQAMHAW0W3AW' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentials:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentials:
CLIENT_ID: XXIS3CL4M12UNBJW4WWAIBB2FH1DFYDSKCFU1N4FXDJBTCFP
CLIENT_SECRET:SILTQ5NCU322DDHLINFUWQ5AS5OI14QX3TVGUQAMHAW0W3AW


In [59]:
# Provide coordinates of Zurich main station (HB)

HB_latitude = 47.3788324
HB_longitude = 8.5366497

In [60]:
# Parameters for the GET request
radius = 8000
query = 'Flower'                  # '4bf58dd8d48988d11b951735'    # 'Flower shop' category
limit = 100

In [61]:
url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&query={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    HB_latitude, 
    HB_longitude, 
    radius, 
    query,
    limit
)
url # display URL

'https://api.foursquare.com/v2/venues/explore?&client_id=XXIS3CL4M12UNBJW4WWAIBB2FH1DFYDSKCFU1N4FXDJBTCFP&client_secret=SILTQ5NCU322DDHLINFUWQ5AS5OI14QX3TVGUQAMHAW0W3AW&v=20180605&ll=47.3788324,8.5366497&radius=8000&query=Flower&limit=100'

Send the GET request and examine the results

In [62]:
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '5d0f6ab68afbe0002d07205f'},
 'response': {'suggestedFilters': {'header': 'Tap to show:',
   'filters': [{'name': 'Open now', 'key': 'openNow'}]},
  'headerLocation': 'Zürich',
  'headerFullLocation': 'Zürich',
  'headerLocationGranularity': 'city',
  'query': 'flower',
  'totalResults': 25,
  'suggestedBounds': {'ne': {'lat': 47.45083247200007,
    'lng': 8.64277960569987},
   'sw': {'lat': 47.30683232799993, 'lng': 8.43051979430013}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '4d2bf76bb818a35d8083b48a',
       'name': 'Bürkliplatz Markt',
       'location': {'address': 'Bürkliplatz',
        'lat': 47.367228240736424,
        'lng': 8.540818691253662,
        'labeledLatLngs': [{'label': 'display',
          'lat': 47.3672282407

From the Foursquare lab in the previous module, we know that all the information is in the *items* key. Before we proceed, let's borrow the **get_category_type** function from the Foursquare lab.

In [63]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

Now we are ready to clean the json and structure it into a *pandas* dataframe.

In [64]:
venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns

filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.head(100)

name   categories        lat       lng
0                         Bürkliplatz Markt       Market  47.367228  8.540819
1                               Chinagarten       Garden  47.354768  8.551098
2                            Stadtgärtnerei       Garden  47.375887  8.499444
3                                Blume 3000  Flower Shop  47.378753  8.538510
4                          Veg And The City  Flower Shop  47.378449  8.531995
5                                   Bubbles         Café  47.372590  8.528307
6                           blumen fitze AG  Flower Shop  47.372091  8.538736
7                             Blumen Krämer  Flower Shop  47.370522  8.535878
8                                   Marsano  Flower Shop  47.369852  8.539071
9                             Blumen & Cafe  Flower Shop  47.370612  8.517354
10                          Blumen Bassetti  Flower Shop  47.378087  8.510347
11                      Blumen Fischer GmbH  Flower Shop  47.370379  8.513337
12                      Blumen Frieden GmbH  Flower Shop  47.378290  8.509368
13                           Wiedikon Point  Flower Shop  47.369267  8.520663
14                              Blumenundso  Flower Shop  47.398460  8.533121
15                      Blumenhaus Nordheim  Flower Shop  47.402923  8.535470
16                               Blumen Art  Flower Shop  47.357513  8.554392
17                          Blumen A. Heini  Flower Shop  47.404638  8.537333
18                      Blumenboutique Goos  Flower Shop  47.369460  8.492068
19                               Café Felix         Café  47.367398  8.544445
20  dickicht blumen + accessoires Gaby Dick  Flower Shop  47.345010  8.529898
21                             Blumen Jakob  Flower Shop  47.402297  8.496373
22                             Blumen Jakob  Flower Shop  47.414004  8.590931
23                         Rosanella Blumen  Flower Shop  47.368474  8.462628
24              Blumen zum selber schneiden  Flower Shop  47.423921  8.499499

In [65]:
# Check the shape of nearby_venues

nearby_venues.shape

(25, 4)

In [66]:
# Drop the two venues which actually don't sell flowers

nearby_venues = nearby_venues[nearby_venues.categories != 'Café']
nearby_venues

name   categories        lat       lng
0                         Bürkliplatz Markt       Market  47.367228  8.540819
1                               Chinagarten       Garden  47.354768  8.551098
2                            Stadtgärtnerei       Garden  47.375887  8.499444
3                                Blume 3000  Flower Shop  47.378753  8.538510
4                          Veg And The City  Flower Shop  47.378449  8.531995
6                           blumen fitze AG  Flower Shop  47.372091  8.538736
7                             Blumen Krämer  Flower Shop  47.370522  8.535878
8                                   Marsano  Flower Shop  47.369852  8.539071
9                             Blumen & Cafe  Flower Shop  47.370612  8.517354
10                          Blumen Bassetti  Flower Shop  47.378087  8.510347
11                      Blumen Fischer GmbH  Flower Shop  47.370379  8.513337
12                      Blumen Frieden GmbH  Flower Shop  47.378290  8.509368
13                           Wiedikon Point  Flower Shop  47.369267  8.520663
14                              Blumenundso  Flower Shop  47.398460  8.533121
15                      Blumenhaus Nordheim  Flower Shop  47.402923  8.535470
16                               Blumen Art  Flower Shop  47.357513  8.554392
17                          Blumen A. Heini  Flower Shop  47.404638  8.537333
18                      Blumenboutique Goos  Flower Shop  47.369460  8.492068
20  dickicht blumen + accessoires Gaby Dick  Flower Shop  47.345010  8.529898
21                             Blumen Jakob  Flower Shop  47.402297  8.496373
22                             Blumen Jakob  Flower Shop  47.414004  8.590931
23                         Rosanella Blumen  Flower Shop  47.368474  8.462628
24              Blumen zum selber schneiden  Flower Shop  47.423921  8.499499

# 10. ADD EXISTING FLOWER SHOPS TO THE MAP OF ZURICH

In [67]:
# Add markers for each flower shop on the Zurich map


for lat, lng, venue in zip(nearby_venues['lat'], nearby_venues['lng'], nearby_venues['name']):
    label = '{}'.format(venue)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=6,
        popup=label,
        color='green',
        fill=True,
        fill_color='green',
        fill_opacity=0.7,
        parse_html=False).add_to(zuri_map1)  
        
zuri_map1

**NOTE:**
- Clicking on any green spot allows to read the name of the flower shop

In [68]:
# Add a 500 circle centered on Altstetten station (top 8 station, ie index number 7 in the dataframe)

latitude = zuri_top_stations_m.stop_lat[7]
longitude = zuri_top_stations_m.stop_lon[7]
label = '{}'.format(zuri_top_stations_m.Haltestellenlangname[7])

folium.Circle(location=[latitude, longitude], radius=1000,
                    popup=label, line_color='#3186cc',
                    fill_color='#3186cc').add_to(zuri_map1)
zuri_map1